### Create Lookup features 

We've learned how to define a target and materialize data using observation tables. Now, let's dive into basic feature engineering.

The most straightforward features we can craft with FeatureByte are known as lookup features. These are either direct columns taken from the source table or simple computations that don't require any aggregations.

In [1]:
import featurebyte as fb

# Set your profile to the tutorial environment
fb.use_profile("tutorial")

catalog_name = "Grocery Dataset Tutorial"
catalog = fb.Catalog.activate(catalog_name)  

21:59:23 | INFO     | Using configuration file at: /Users/gxav/.featurebyte/config.yaml


21:59:23 | INFO     | Active profile: tutorial (https://tutorials.featurebyte.com/api/v1)


21:59:23 | WARNING  | Remote SDK version (0.5.0.dev6) is different from local (0.5.0.dev1). Update local SDK to avoid unexpected behavior.


21:59:23 | INFO     | No catalog activated.


21:59:23 | INFO     | 6 feature lists, 31 features deployed


...

21:59:24 | INFO     | Active profile: tutorial (https://tutorials.featurebyte.com/api/v1)


21:59:24 | WARNING  | Remote SDK version (0.5.0.dev6) is different from local (0.5.0.dev1). Update local SDK to avoid unexpected behavior.


21:59:24 | INFO     | No catalog activated.


21:59:25 | INFO     | 6 feature lists, 31 features deployed


21:59:25 | INFO     | Catalog activated: Grocery Dataset Tutorial


In [2]:
# Get view from GROCERYCUSTOMER scd table.
grocerycustomer_view = catalog.get_view("GROCERYCUSTOMER")

#### Create Lookup feature

In [3]:
# Create lookup feature from DateOfBirth column for customer entity.
customer_dateofbirth = grocerycustomer_view["DateOfBirth"].as_feature("CUSTOMER_DateOfBirth")

#### Derive Age at the point-in-time of the request observation

In [4]:
# Derive Age from the point-in-time and the date of birth.
customer_age = (
    (fb.RequestColumn.point_in_time()- customer_dateofbirth).dt.day / 365.25
).floor()
# Name feature
customer_age.name = "CUSTOMER_Age"

In [5]:
# Transform age into a 5 year age band.
customer_age_band = (
    ((customer_age + 1) / 5).ceil() - 1
) * 5
customer_age_band = (
    customer_age_band.astype(str)
     + "-" + (customer_age_band + 4).astype(str)
)
# Name feature
customer_age_band.name = "CUSTOMER_Age_band"

#### Preview feature
We will use observation table we created in previous tutorial here.

In [6]:
# Check the primary entity of the feature'
customer_age.primary_entity

 {
   'name': 'customer',
   'created_at': '2023-09-11T13:56:58.863000',
   'updated_at': '2023-09-11T13:57:16.943000',
   'description': None,
   'serving_names': [
     'GROCERYCUSTOMERGUID'
   ],
   'catalog_name': 'Grocery Dataset Tutorial'
 }]

In [7]:
# Get observation table: 'Preview Table with 10 Customers'
preview_table = catalog.get_observation_table("Preview Table with 10 Customers").to_pandas()

In [8]:
# Preview CUSTOMER_Age
customer_age.preview(preview_table)

POINT_IN_TIME                   GROCERYCUSTOMERGUID  CUSTOMER_Age
0 2022-07-21 12:50:21  dd0c74f0-9ba8-4ca9-bd84-8148095aa38a            53
1 2022-11-10 15:57:20  0401635c-e6ab-4525-bb5d-00aba7f6d0c4            30
2 2022-08-14 19:00:14  54d86ef6-f9b8-40e2-9162-a60bd1b705db            21
3 2022-07-12 08:02:04  4eb4ee84-ee13-4eec-9c26-61b6eb4ba35b            69
4 2022-12-13 08:15:49  1e866814-e5a6-475d-87e3-b53377cc005b            59
5 2023-04-26 16:52:34  48072b52-39cf-452c-8531-02cc4d0fc32e            40
6 2023-03-01 11:31:00  081f111a-598b-43ae-a28a-3a5dc3d2a091            63
7 2023-01-19 16:33:33  f3415165-754c-40b6-af17-06ef952a3fa1            20
8 2023-04-11 19:07:26  d0ea14bf-038a-4ae5-887e-e2d4d68dd8f6            40
9 2023-04-10 08:24:27  69d8718e-8c4a-4264-8edf-e0ffc1ef4737            30

In [9]:
# Preview CUSTOMER_Age_band
customer_age_band.preview(preview_table)

POINT_IN_TIME                   GROCERYCUSTOMERGUID CUSTOMER_Age_band
0 2022-07-21 12:50:21  dd0c74f0-9ba8-4ca9-bd84-8148095aa38a             50-54
1 2022-11-10 15:57:20  0401635c-e6ab-4525-bb5d-00aba7f6d0c4             30-34
2 2022-08-14 19:00:14  54d86ef6-f9b8-40e2-9162-a60bd1b705db             20-24
3 2022-07-12 08:02:04  4eb4ee84-ee13-4eec-9c26-61b6eb4ba35b             65-69
4 2022-12-13 08:15:49  1e866814-e5a6-475d-87e3-b53377cc005b             55-59
5 2023-04-26 16:52:34  48072b52-39cf-452c-8531-02cc4d0fc32e             40-44
6 2023-03-01 11:31:00  081f111a-598b-43ae-a28a-3a5dc3d2a091             60-64
7 2023-01-19 16:33:33  f3415165-754c-40b6-af17-06ef952a3fa1             20-24
8 2023-04-11 19:07:26  d0ea14bf-038a-4ae5-887e-e2d4d68dd8f6             40-44
9 2023-04-10 08:24:27  69d8718e-8c4a-4264-8edf-e0ffc1ef4737             30-34

In [10]:
# Save features to catalog 
customer_age.save()
customer_age_band.save()

Working... |                                        | ▁▃▅ 0% in 0s (~0s, 0.0%/s)

Working... |                                        | ▂▄▆ 0% in 0s (~0s, 0.0%/s)

Working... |                                        | ▃▅▇ 0% in 0s (~0s, 0.0%/s)

Working... |                                        | ▄▆█ 0% in 0s (~0s, 0.0%/s)

Working... |                                        | ▅▇▇ 0% in 0s (~0s, 0.0%/s)

...

Working... |████████████████████████████████████████| ▇▅▃ 100% in 7s (~0s, 0.2%/

Working... |████████████████████████████████████████| ▆▄▂ 100% in 7s (~0s, 0.2%/

Working... |████████████████████████████████████████| ▅▃▁ 100% in 7s (~0s, 0.2%/

Working... |████████████████████████████████████████| ▄▂▂ 100% in 7s (~0s, 0.1%/

Done! |████████████████████████████████████████| 100% in 6.8s (0.15%/s)         

In [11]:
# Add description
customer_age.update_description("Age of the customer.")
customer_age_band.update_description("Age Band of the customer.")

#### Check feature definition files (same as definition files we discussed in target tutorial)

In [12]:
customer_age.definition

'# Generated by SDK version: 0.5.0.dev6\nfrom bson import ObjectId\nfrom featurebyte import SCDTable\nfrom featurebyte.api.request_column import RequestColumn\n\n\n# scd_table name: "GROCERYCUSTOMER"\nscd_table = SCDTable.get_by_id(ObjectId("64ff1c8f0d5bfbfb21bce789"))\nscd_view = scd_table.get_view(\n    view_mode="manual",\n    drop_column_names=["record_available_at", "CurrentRecord"],\n    column_cleaning_operations=[],\n)\ngrouped = scd_view.as_features(\n    column_names=["DateOfBirth"],\n    feature_names=["CUSTOMER_DateOfBirth"],\n    offset=None,\n)\nfeat = grouped["CUSTOMER_DateOfBirth"]\nrequest_col = RequestColumn.point_in_time()\nfeat_1 = ((request_col - feat).dt.day / 365.25).floor()\nfeat_1.name = "CUSTOMER_Age"\noutput = feat_1\noutput.save(_id=ObjectId("64ff1d4182feedb4dc91333f"))\n'

In [13]:
customer_age_band.definition

'# Generated by SDK version: 0.5.0.dev6\nfrom bson import ObjectId\nfrom featurebyte import SCDTable\nfrom featurebyte.api.request_column import RequestColumn\n\n\n# scd_table name: "GROCERYCUSTOMER"\nscd_table = SCDTable.get_by_id(ObjectId("64ff1c8f0d5bfbfb21bce789"))\nscd_view = scd_table.get_view(\n    view_mode="manual",\n    drop_column_names=["record_available_at", "CurrentRecord"],\n    column_cleaning_operations=[],\n)\ngrouped = scd_view.as_features(\n    column_names=["DateOfBirth"],\n    feature_names=["CUSTOMER_DateOfBirth"],\n    offset=None,\n)\nfeat = grouped["CUSTOMER_DateOfBirth"]\nrequest_col = RequestColumn.point_in_time()\nfeat_1 = ((request_col - feat).dt.day / 365.25).floor()\nfeat_1.name = "CUSTOMER_Age"\nfeat_2 = ((((feat_1 + 1) / 5).ceil() - 1) * 5).astype(str) + "-"\nfeat_3 = ((((feat_1 + 1) / 5).ceil() - 1) * 5) + 4\nfeat_4 = feat_2 + feat_3.astype(str)\nfeat_4.name = "CUSTOMER_Age_band"\noutput = feat_4\noutput.save(_id=ObjectId("64ff1d4682feedb4dc913349"))\n'

### Concepts in this tutorial
- [More on features](https://docs.featurebyte.com/latest/about/glossary/#related-to-feature-declaration)
- [More on lookup features](https://docs.featurebyte.com/latest/about/glossary/#lookup-features)
- [More about point-in-time](https://docs.featurebyte.com/latest/about/glossary/#point-in-time)

#### SDK reference for
- [Feature](https://docs.featurebyte.com/latest/reference/core/feature/)
- [ViewColumn.as_feature()](https://docs.featurebyte.com/latest/reference/featurebyte.api.view.ViewColumn.as_feature/)
- [RequestColumn.point_in_time](https://docs.featurebyte.com/latest/reference/featurebyte.api.request_column.RequestColumn.point_in_time/)
- [Feature.preview()](https://docs.featurebyte.com/latest/reference/featurebyte.api.feature.Feature.preview/)
- [Feature.save()](https://docs.featurebyte.com/latest/reference/featurebyte.api.feature.Feature.save/)